In [11]:
import sys
import os
import importlib
import numpy
import random
import SimpleITK
import datetime

nixSuite=os.path.join(os.path.expanduser('~'),'software','src','nixSuite')
sys.path.append(os.path.join(nixSuite,'wrapper'))
import nixWrapper
nixWrapper.loadLibrary('labkeyInterface')
import labkeyInterface
import labkeyDatabaseBrowser
import labkeyFileBrowser


nixWrapper.loadLibrary('orthancInterface')
import orthancInterface
import orthancDatabaseBrowser
import orthancFileBrowser

loadLibrary
remoteSourcesURL https://git0.fmf.uni-lj.si/studen/nixSuite/raw/master/remoteResources/resources.json
{'labkeyInterface': {'url': 'https://git0.fmf.uni-lj.si/studen/labkeyInterface/archive/master.zip', 'branch': 'master', 'modules': []}, 'irAEMM': {'url': 'https://git0.fmf.uni-lj.si/studen/iraemm/archive/master.zip', 'branch': 'master', 'modules': ['iraemmBrowser']}, 'SlicerLabkeyExtension': {'url': 'https://git0.fmf.uni-lj.si/studen/SlicerLabkeyExtension/archive/SlicerExtensionIndex.zip', 'branch': 'SlicerExtensionIndex', 'modules': ['labkeyBrowser']}, 'limfomiPET': {'url': 'https://git0.fmf.uni-lj.si/studen/limfomiPET/archive/master.zip', 'branch': 'master', 'modules': ['imageBrowser', 'segmentationBrowser']}, 'parseConfig': {'url': 'https://git0.fmf.uni-lj.si/studen/parseConfig/archive/master.zip', 'branch': 'master', 'modules': []}, 'orthancInterface': {'url': 'https://git0.fmf.uni-lj.si/studen/orthancInterface/archive/master.zip', 'branch': 'master', 'modules': []}, 'd

In [2]:
def initDB(site,returnFB=False):
    net=labkeyInterface.labkeyInterface()
    fconfig=os.path.join(os.path.expanduser('~'),'.labkey','{}.json'.format(site))
    net.init(fconfig)
    net.getCSRF()
    if not returnFB:
        return labkeyDatabaseBrowser.labkeyDB(net)
    return labkeyDatabaseBrowser.labkeyDB(net),labkeyFileBrowser.labkeyFileBrowser(net)

def initOrthanc(site,returnFB=False):
    net=orthancInterface.orthancInterface()
    fconfig=os.path.join(os.path.expanduser('~'),'.labkey','{}.json'.format(site))
    net.init(fconfig)
    if not returnFB:
        return orthancDatabaseBrowser.orthancDB(net)
    return orthancDatabaseBrowser.orthancDB(net),orthancFileBrowser.orthancFileBrowser(net)



In [3]:
db,fb=initDB('onko-nix',returnFB=True)
odb,ofb=initOrthanc('onko-nix',returnFB=True)

User: andrej studen CSRF: f7abf32866c67a6f503e050311032978


In [35]:
def parsePos(x):
    return [float(y) for y in x.split('\\')]

def parseOrientation(x):
    z=[float(y) for y in x.split('\\')]
    O=[z[0:3],z[3:6]]
    O.append(list(numpy.cross(numpy.array(O[0]),numpy.array(O[1]))))
    return O

def getGeometry(code,odb,seriesId):
    #imagepositionpatient 0020-0032
    #imageorientationpatient 0020-0037
    #pixelSpacing 0028-0030
    #instance number 0020-0013
    #sliceThickness 0018-0050
    
    sd=odb.getData('series',seriesId)
    firstId=sd['Instances'][0] 
    
    ior=parseOrientation(odb.getDicomField(firstId,'0020-0037'))
    #spacing
    ips=parsePos(odb.getDicomField(firstId,'0028-0030'))
    ist=parsePos(odb.getDicomField(firstId,'0018-0050')) 
    #don't use slice thickness for pixel spacing
    #ips.append(ist[0])
    
    ipos=[parsePos(odb.getDicomField(y,'0020-0032')) for y in sd['Instances']] 
    #guess spacing from ipos
    m=[numpy.dot(numpy.array(ior[2]),numpy.array(x)) for x in ipos] 
    #sort array
    m1=numpy.sort(m)
    dm=m1[1:]-m1[:-1]
    zSpc=numpy.average(dm)
    zDev=numpy.std(dm)
    print(f'sliceThickness={zSpc} +- {zDev}')
    ips.append(zSpc)
    
    #direction, ie. scaled orientation
    #copy orientation to direction
    xdir=[y for y in ior]
    for i in range(3):
        xdir[i]=[ips[i]*w for w in xdir[i]]
    
    #find minimum from original array to idenfify lower slice
    im=numpy.argmin(numpy.array(m))
    print(im)
    org=ipos[im]
    print(org)
    print(xdir)
    return {f'{code}origin':org,f'{code}orientation':xdir}
    
        
        
def getFile(db,odb):
    project='/iPNUMMretro/Study'
    schema='study'
    query='Imaging1'
    #coreDir=os.path.join(os.path.expanduser('~'),'temp')
    coreDir=os.path.join('Z:')
    ds=db.selectRows(project,schema,query,[])
    rows=ds['rows'][0:1]
    imgs={'CT':'CT_orthancId','PET':'PETWB_orthancId'}
    for r in rows:
        code=r['pseudoCode']
        doUpdate=False
        if not code:
            code='{:16x}'.format(random.randrange(16**16))
            r['pseudoCode']=code
            doUpdate=True
            
        fname=os.path.join(coreDir,f'{code}.npz')
        arr={}
        #debug  don't load array
        iSUV={x:getSUVfactor(odb,r[imgs[x]]) for x in imgs}
        arr.update({x:iSUV[x]*numpy.load(odb.getNumpy('series',r[imgs[x]])) for x in imgs})
        #debug don't calculate geometry
        igeo={x:getGeometry(x,odb,r[imgs[x]]) for x in imgs}
        #debug skip saving
        #continue
        _={arr.update(igeo[x]) for x in igeo}
        #print(arr)
        
        
        numpy.savez_compressed(fname,**arr)
        if doUpdate:
            db.modifyRows('update',project,schema,query,[r])
        
def mergeDateAndTime(date,time):
    time=time.replace(' ','')
    dateTimeStr=' '.join([date,time])
    #print(f'[{date}] [{time}] [{dateTimeStr}]')
    dt=datetime.datetime.strptime(dateTimeStr,'%Y%m%d %H%M%S.%f')
    #print(dt)
    return dt
        
def getSUVfactor(odb,seriesId):
    sd=odb.getData('series',seriesId)
    orthancId=sd['Instances'][0] 
    
    MODALITY='0008-0060'
    PATIENT_WEIGHT='0010-1030'
    RADIOPHARMACEUTICAL_STARTTIME='0054-0016/0/0018-1072'
    RADIONUCLIDE_TOTALDOSE='0054-0016/0/0018-1074'
    RADIONUCLIDE_HALFLIFE='0054-0016/0/0018-1075'
    RADIOPHARMACEUTICAL_STARTDATETIME='0054-0016/0/0018-1078'
    SERIES_TIME='0008-0031'
    SERIES_DATE='0008-0021'
    modality=odb.getDicomField(orthancId,MODALITY)
    if modality!='PT':
        print('Returning 1')
        return 1
    weight = float(odb.getDicomField(orthancId,PATIENT_WEIGHT))
    #print(weight)
    halfLife = float(odb.getDicomField(orthancId,RADIONUCLIDE_HALFLIFE))#seconds
    #print(halfLife)
    injDose = float(odb.getDicomField(orthancId,RADIONUCLIDE_TOTALDOSE))#in Bq
    #print(injDose)
    #two options for time of activity measurement (full date time or time only, then match it with studyDate)
    #injDateTime = odb.getDicomField(orthancId,RADIOPHARMACEUTICAL_STARTDATETIME)
    #if troubles:
    injDateTime = mergeDateAndTime(odb.getDicomField(orthancId,SERIES_DATE),
            odb.getDicomField(orthancId,RADIOPHARMACEUTICAL_STARTTIME))
    scanDateTime=mergeDateAndTime(odb.getDicomField(orthancId,SERIES_DATE),
                                  odb.getDicomField(orthancId,SERIES_TIME))
    t=(scanDateTime-injDateTime).total_seconds()
    scanDose = injDose*numpy.exp(-(numpy.log(2)*t)/halfLife);
    SUV_factor = 1/((scanDose/weight)*0.001);
    print(SUV_factor)
    return SUV_factor

    
getFile(db,odb)
    

Returning 1
0.0003862617854116126
sliceThickness=2.0 +- 0.0
928
[-389.23828125, -569.73828125, -941.0]
[[1.5234375, 0.0, 0.0], [0.0, 1.5234375, 0.0], [0.0, 0.0, 2.0]]
sliceThickness=3.0 +- 0.0
0
[-403.656, -588.125, -942.0]
[[4.07283, 0.0, 0.0], [0.0, 4.07283, 0.0], [0.0, 0.0, 3.0]]


In [36]:
def convertToITK(dt,label):
    imgArray=dt[label]
    org=dt['{}origin'.format(label)]
    orient=dt['{}orientation'.format(label)]
    spacing=[numpy.linalg.norm(x) for x in orient]
    print(spacing)
    orient=[orient[i]/spacing[i] for i in range(3)]
    direction=numpy.reshape(orient,9)
    print(direction)
    img = SimpleITK.GetImageFromArray(imgArray)
    img.SetOrigin(org)
    img.SetDirection(direction)
    img.SetSpacing(spacing)
    return img

#convert to SimpleITKimage to display it
infile=os.path.join('Z:','6ebf549213805ee0.npz')
dt=numpy.load(infile)
ct=convertToITK(dt,'CT')
pet=convertToITK(dt,'PET')
outdir=os.path.join('Z:')
SimpleITK.WriteImage(ct,os.path.join(outdir,'CT.nii.gz'))
SimpleITK.WriteImage(pet,os.path.join(outdir,'PET.nii.gz'))
del ct
del pet



[1.5234375, 1.5234375, 2.0]
[1. 0. 0. 0. 1. 0. 0. 0. 1.]
[4.07283, 4.07283, 3.0]
[1. 0. 0. 0. 1. 0. 0. 0. 1.]
